In [1]:
from typing import Optional

from tqdm import trange
import torch
from torch import Tensor
from torch_geometric.data import Data
from torch_geometric.loader import DataLoader
from torch_geometric.nn import MessagePassing
from torch_geometric.experimental import disable_dynamic_shapes
from torch_geometric.nn.aggr import Aggregation
from torch_geometric.utils import coalesce, degree, cumsum
from torch_geometric import EdgeIndex

import pathpyG as pp
pp.config['torch']['device'] = 'cuda'

In [2]:
# Example with walks as node sequences
g = pp.Graph.from_edge_list([('a', 'b'), ('b', 'c'), ('a', 'c')])
dags = pp.DAGData(mapping = g.mapping)

dags.append_walk(('a', 'b', 'c'), weight=1.0)
dags.append_walk(('a', 'c'), weight = 2.0)
print(dags)

DAGData with 2 dags with total weight 3.0


In [3]:
# Example with walks as edge indices (with no mapping)
dags = pp.DAGData()
dags.append_dag(torch.tensor([[3,0,1],[0,1,2]]))
dags.append_dag(torch.tensor([[1,0,2],[0,2,0]]))
dags.append_dag(torch.tensor([[0,1],[1,2]]))
print(dags)

DAGData with 3 dags with total weight 3.0


In [4]:
# Example with mix of walks or dags
dags = pp.DAGData(mapping = g.mapping)

dags.append_dag(torch.tensor([[0,0,1],[1,2,2]]))
dags.append_walk(('a', 'b', 'c'))
print(dags)

DAGData with 2 dags with total weight 2.0


In [5]:
m = pp.MultiOrderModel.from_DAGs(dags, max_order=2)

In [6]:
print(m.layers[1].data.edge_index)
print(m.layers[1].data.node_sequences)
print(m.layers[1].mapping)

EdgeIndex([[0, 0, 1],
           [2, 1, 2]], device='cuda:0', sparse_size=(3, 3), nnz=3,
          sort_order=row)
tensor([[0],
        [1],
        [2]], device='cuda:0')
a -> 0
b -> 1
c -> 2



In [7]:
print(m.layers[2].data.edge_index)
print(m.layers[2].data.node_sequences)
print(m.layers[2].mapping)

EdgeIndex([[0],
           [2]], device='cuda:0', sparse_size=(3, 3), nnz=1, sort_order=row)
tensor([[0, 1],
        [0, 2],
        [1, 2]], device='cuda:0')
('a', 'b') -> 0
('a', 'c') -> 1
('b', 'c') -> 2



In [8]:
# Real-world example
dags = pp.DAGData.from_ngram('../data/tube_paths_train.ngram')
print(dags)

DAGData with 61748 dags with total weight 2147865.0


In [9]:
m = pp.MultiOrderModel.from_DAGs(dags, max_order=10)

In [10]:
print(m.layers[3].mapping)

('Southwark', 'Waterloo', 'Embankment') -> 0
('Southwark', 'Waterloo', 'Westminster') -> 1
('Southwark', 'Waterloo', 'Lambeth North') -> 2
('Southwark', 'Waterloo', 'Kennington') -> 3
('Southwark', 'London Bridge', 'Bank / Monument') -> 4
('Southwark', 'London Bridge', 'Bermondsey') -> 5
('Southwark', 'London Bridge', 'Borough') -> 6
('Waterloo', 'Southwark', 'London Bridge') -> 7
('Waterloo', 'Embankment', 'Temple') -> 8
('Waterloo', 'Embankment', 'Charing Cross') -> 9
('Waterloo', 'Westminster', 'Green Park') -> 10
('Waterloo', 'Westminster', "St. James's Park") -> 11
('Waterloo', 'Lambeth North', 'Elephant & Castle') -> 12
('Waterloo', 'Kennington', 'Elephant & Castle') -> 13
('Waterloo', 'Kennington', 'Oval') -> 14
('Liverpool Street', 'Bank / Monument', 'Tower Hill') -> 15
('Liverpool Street', 'Bank / Monument', 'London Bridge') -> 16
('Liverpool Street', 'Bank / Monument', "St. Paul's") -> 17
('Liverpool Street', 'Bank / Monument', 'Cannon Street') -> 18
('Liverpool Street', 'Moo

In [11]:
pp.plot(m.layers[10], node_label=list(map(str, m.layers[1].data.node_sequences.tolist())))

In [12]:
dags.map_node_seq(m.layers[10].data.node_sequences[5].tolist())

['Southwark',
 'Waterloo',
 'Westminster',
 'Green Park',
 'Bond Street',
 'Baker Street',
 'Finchley Road',
 'HarrowOnTheHill',
 'Moor Park',
 'Northwood']

In [13]:
print(m.layers[2].data.edge_index)

EdgeIndex([[  0,   0,   0,  ..., 644, 644, 645],
           [  3,   4,   5,  ..., 504, 505, 582]], device='cuda:0',
          sparse_size=(646, 646), nnz=1139, sort_order=row)


In [14]:
print(m.layers[2].data.edge_weights)

AttributeError: 'GlobalStorage' object has no attribute 'edge_weights'

In [ ]:
print(m.layers[2].data.node_sequences)

tensor([[  0,   1],
        [  0, 115],
        [  1,   0],
        ...,
        [265, 130],
        [266, 194],
        [266, 235]], device='cuda:0')
